In [ ]:
# JSON-export öffnen
import json
path = "export.json"
with open(path,
          encoding = "utf-8") as file:
  data = json.loads(file.read())

In [ ]:
# JSON-Hierarchie in flache Datenstruktur umwandeln
table = ({**ord, **subOrd, **item}
  for ord in data['orders']['orders']
  for subOrd in ord['subOrders']
  for item in subOrd['lineItems'])

In [ ]:
# Daten in einen DataFrame importieren
import pandas
df = pandas.DataFrame(table)

# Spalte mit interpretiertem Zeitstempel ergänzen
df['date'] = pandas.to_datetime(
  df['creationDate']
)

In [ ]:
# Behalte nur die genannten Spalten (in der genannten Reihenfolge)
df = df[['date', 'orderId',
  'orderValue', 'title', 'price',
  'quantity', 'totalPrice']]

In [ ]:
# Unnütze Einträge aussortieren
dummies = ["Enthaltene Pfandbeträge",
  "Getränke-Sperrgutaufschlag",
  "TimeSlot"]
df = df[~df['title'].isin(dummies)]

In [ ]:
# Datumsspalte zum Index erklären
df = df.set_index(['date'])

In [ ]:
df

In [ ]:
# Monatliche Einkaufssummen plotten
# Die folgenden Zeilen auskommentieren, um die Auflösung der Grafik anzupassen

#import matplotlib.pyplot as plt
#plt.rcParams['figure.dpi'] = 300
#plt.rcParams['savefig.dpi'] = 300

df.resample('m').sum()['totalPrice'].plot(kind='bar')

In [ ]:
# Nach Produkttiteln gruppieren
df = df.groupby('title') 

# Minimum und Maximum jedes Produktes auswählen
min = df.min()['price']
max = df.max()['price']

# Fluktuation berechnen, sortieren und ausgeben
fluc = (max - min) / (max + min)
fluc.sort_values(ascending=False).to_frame('Fluctuation')

In [ ]:
# Unit-Klasse importieren und damit experimentieren
from units import Unit, UnitType

p = Unit.parse("Pils 24x0,33l")
w1 = Unit.parse("Hefeweizen 5L Fass")
w2 = Unit.parse("Weißbier 6x0,5l")
p > w1 + w2 # Ergibt False

In [ ]:
# Produktgruppen nach Anzahl summieren
df = df.sum()[['quantity']]

# Eine Spalte mit verarbeiteten Einheiten ergänzen
df['unit'] = df.index.map(Unit.parse)

# Produkte aussortieren, bei denen keine Einheit geparst werden konnte
df = df[df['unit'].notna()]

# Eine Spalte mit der Gesamtmenge (Einheit mal Anzahl) ergänzen
df['total'] = df['unit'] * df['quantity']
df

In [ ]:
# Filtere nach Produkten mit Gewichtsangaben
df_weight = df[df['unit'].map(
  lambda unit: unit.unit_type == UnitType.WEIGHT
)]
# Sortiere die gefilterte Liste absteigend nach der Gesamtmenge
df_weight.sort_values('total', ascending = False)

In [ ]:
# Das gleiche nochmal mit Produkten mit Volumenangaben
df_volume = df[df['unit'].map(
  lambda unit: unit.unit_type == UnitType.VOLUME
)]
df_volume.sort_values('total', ascending = False)